## Install Dependencies

In [1]:
! pip install -U datasets

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 510.5/510.5 kB 6.4 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 116.3/116.3 kB 7.0 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 194.1/194.1 kB 5.3 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 134.8/134.8 kB 6.2 MB/s eta 0:00:00


In [10]:
import pandas as pd
from datasets import load_dataset, DatasetDict
from huggingface_hub import notebook_login
from sklearn.model_selection import train_test_split

## Preprocess data

In [30]:
df = pd.read_csv("cleaned_data.csv", usecols=["text", "sentiment"])
df.rename(columns={"sentiment": "label"}, inplace=True)
df.head()

text     label
0  If you decide to eat here, just be aware it is...   Neutral
1  I am a long term frequent customer of this est...  Negative
2  Loved this tour! I grabbed a groupon and the p...  Positive
3  Love going here for happy hour or dinner!  Gre...  Positive
4  Great staff always helps and always nice. Alwa...  Positive

In [31]:
df["label"].value_counts()

label
Positive    101121
Negative     36346
Neutral      16846
Name: count, dtype: int64

In [32]:
def sentiment_to_int(sentiment: str) -> int:
    if sentiment.lower() == "negative":
        return 0
    if sentiment.lower() == "neutral":
        return 1
    if sentiment.lower() == "positive":
        return 2
    raise Exception(f"{sentiment} is not a valid value")

In [33]:
df["label"] = df["label"].apply(sentiment_to_int)
df.head()

text  label
0  If you decide to eat here, just be aware it is...      1
1  I am a long term frequent customer of this est...      0
2  Loved this tour! I grabbed a groupon and the p...      2
3  Love going here for happy hour or dinner!  Gre...      2
4  Great staff always helps and always nice. Alwa...      2

In [34]:
df = df.sample(frac=1).reset_index(drop=True)

In [35]:
train_df, test_eval_df = train_test_split(df, test_size=0.5)
test_df, eval_df = train_test_split(test_eval_df, test_size=0.5)

In [36]:
train_df.shape, test_df.shape, eval_df.shape

((77156, 2), (38578, 2), (38579, 2))

In [37]:
train_df["label"].value_counts(), test_df["label"].value_counts(), eval_df[
    "label"
].value_counts()

(label
 2    50426
 0    18120
 1     8610
 Name: count, dtype: int64,
 label
 2    25388
 0     9096
 1     4094
 Name: count, dtype: int64,
 label
 2    25307
 0     9130
 1     4142
 Name: count, dtype: int64)

## Save the data

In [38]:
train_df.to_csv("train.csv", index=False)
test_df.to_csv("test.csv", index=False)
eval_df.to_csv("eval.csv", index=False)

## Uploading to Hub

In [39]:
notebook_login()

In [40]:
yelp_dataset = DatasetDict.from_csv(
    {"train": "train.csv", "test": "test.csv", "eval": "eval.csv"}
)

Generating train split: 0 examples [00:00, ? examples/s]

Generating test split: 0 examples [00:00, ? examples/s]

Generating eval split: 0 examples [00:00, ? examples/s]

In [41]:
yelp_dataset.push_to_hub("noahnsimbe/yelp-dataset")

/usr/local/lib/python3.10/dist-packages/huggingface_hub/utils/_token.py:88: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


Uploading the dataset shards:   0%|          | 0/1 [00:00<?, ?it/s]

Creating parquet from Arrow format:   0%|          | 0/78 [00:00<?, ?ba/s]

Uploading the dataset shards:   0%|          | 0/1 [00:00<?, ?it/s]

Creating parquet from Arrow format:   0%|          | 0/39 [00:00<?, ?ba/s]

Uploading the dataset shards:   0%|          | 0/1 [00:00<?, ?it/s]

Creating parquet from Arrow format:   0%|          | 0/39 [00:00<?, ?ba/s]

README.md:   0%|          | 0.00/5.01k [00:00<?, ?B/s]

CommitInfo(commit_url='https://huggingface.co/datasets/noahnsimbe/yelp-dataset/commit/56fa2d9c0bafcf1c9ed9f2ff6859fa67d14889b3', commit_message='Upload dataset', commit_description='', oid='56fa2d9c0bafcf1c9ed9f2ff6859fa67d14889b3', pr_url=None, pr_revision=None, pr_num=None)

## Testing

In [42]:
yelp_dataset = load_dataset("noahnsimbe/yelp-dataset")

Generating train split:   0%|          | 0/77156 [00:00<?, ? examples/s]

Generating test split:   0%|          | 0/38578 [00:00<?, ? examples/s]

Generating eval split:   0%|          | 0/38579 [00:00<?, ? examples/s]

In [43]:
yelp_train_df = pd.DataFrame(yelp_dataset["train"])
yelp_test_df = pd.DataFrame(yelp_dataset["test"])
yelp_eval_df = pd.DataFrame(yelp_dataset["eval"])

In [44]:
yelp_train_df.head()

text  label
0  This review is long overdue. From 6/15/13-6/17...      2
1  Happy, Happy to find awesome Tres Leches Cake!...      2
2  Here's what many people don't understand.. In ...      0
3  I really enjoyed the pick 2 mix and match opti...      2
4  Hotel is very nice. Nice view. Outside of appe...      0

In [45]:
yelp_test_df.head()

text  label
0  Staying here for a sales meeting. Absolutely a...      2
1  The food was incredibly good, the waiter was t...      1
2  I have gone back- the food is the same, prices...      1
3  The best ingredients! The pizzas are so delici...      2
4  An open letter to Tony Luke! \nDear Sir,\nI ha...      0

In [46]:
yelp_eval_df.head()

text  label
0  Absolutely the worst service! I've been callin...      0
1  This is my second time to this location and th...      2
2  I think they are always striving to improve bu...      1
3  We are so very excited to return to UCSB Famil...      2
4  This is your typical extended stay type place ...      2

In [47]:
yelp_test_df["label"].value_counts(), yelp_train_df[
    "label"
].value_counts(), yelp_eval_df["label"].value_counts()

(label
 2    25388
 0     9096
 1     4094
 Name: count, dtype: int64,
 label
 2    50426
 0    18120
 1     8610
 Name: count, dtype: int64,
 label
 2    25307
 0     9130
 1     4142
 Name: count, dtype: int64)